# Hvordan optimere kode med Numba og `@njit`

- Før du bruker Numba, les igjennom dette dokumentet samt Numba-delen av det numeriske kompendiet: /studier/emner/matnat/astro/AST2000/h18/undervisningsmateriell_h2018/Numerical%20Compendium/numba.pdf Det vil sannsynligvis ta deg mindre tid enn å løse feilene som typisk oppstår ved å ikke gjøre det.

- Første bud for all optimering: **Skriv først kode som virker!** Ikke tenk på ytelsen, bare gjør ting så rett frem som mulig og kjør tester med lite belastning. Deretter kan du gjøre det raskere hvis det absolutt er nødvendig (ofte er det ikke det). Når du modifiserer en funksjon for å få den raskere, sjekk resultatene fortløpende mot den trege versjonen som du vet stemmer.

- Når det kommer til Numba betyr dette at du **ikke** slenger på `@njit` uten at du først er **sikker på** at funksjonen fungerer og at den går for sakte.

- @njit er det samme som @jit(nopython=True). Det kan hende Numba ikke klarer å kompilere koden din (gjøre den raskere). Med vanlig @jit vil Numba bare la koden din være treig, uten å fortelle deg om det. Med @njit vil Numba gi en feilmelding om at den ikke klarte å kompilere koden, det er mye bedre.

- Koden du skal gjøre raske med @njit må være inni en funksjon - det kan ofte være en god ide å flytte en liten del av koden inn i en ny funksjon, og bruke @njit på denne.

- Numba funker best dersom koden din består av "enkel" python. Du kan fint bruke Numpy-arrays men du burde unngå vektorisert Numpy kode, og heller bruke "vanlig" Python kode med loops osv. Numba er somregel raskere enn Numpy-vektorisering!

- Du kan også parallelisere koden din med "prange" istedenfor "range", så lenge loop-iterasjonene skriver til forskjellig data, og iterasjonene er uavhengige!

## Bruk `@jit` på trege funksjoner med arrayer og løkker

In [156]:
import numpy as np
import time
from numba import njit  # njit er det samme som jit(nopython=True). Du burde alltid bruke dette.
from numba import prange  # prange er en versjon av range, og som kan brukes til å gjøre loops parallelle.

Her er en Python-funksjon med mye beregning, som bare bruker enkle objekter som arrayer og skalarer.

In [157]:
def fibonacci(N):
    """
    Computes the Fibonacci sequence with N elements.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

Vi kan måle tiden den bruker på å regne ut de 1000 første tallene i Fibonacci-følgen.

In [155]:
%timeit fibonacci(1000)

134 μs ± 628 ns per loop (mean ± std. dev. of 7 runs, 10,000 loops each)


Men hva hvis vi trenger å gjøre dette raskere?

`fibonacci` er et godt eksempel på en funksjon som egner seg til å gjøres raskere med Numba. Ved å sette inn `@njit` over funksjonen, kan vi be Numba gjøre om hele funksjonen til effektiv maskinkode rett før den skal kalles. JIT står for "Just-In-Time compilation".

In [151]:
@njit
def fibonacci_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

In [152]:
%timeit fibonacci_jit(1000) # ~150 times faster than fibonacci

2.08 μs ± 17.8 ns per loop (mean ± std. dev. of 7 runs, 100,000 loops each)


## Unngå `@njit` på raske funksjoner

In [158]:
def fibonacci_cheat(N):
    """
    Returns the Fibonacci sequence with N=5 elements.
    """
    assert N == 5, 'N must be 5'
    return np.array([0.0, 1.0, 1.0, 2.0, 3.0])

In [159]:
%timeit -r1 -n1 fibonacci_cheat(5)

12.5 μs ± 0 ns per loop (mean ± std. dev. of 1 run, 1 loop each)


In [160]:
@njit
def fibonacci_cheat_jit(N):
    """
    Returns the Fibonacci sequence with N=5 elements.
    """
    assert N == 5, 'N must be 5'
    return np.array([0.0, 1.0, 1.0, 2.0, 3.0])

In [161]:
%timeit -r1 -n1 fibonacci_cheat_jit(5) # ~50 000 times slower than fibonacci_cheat for first call!

62.7 ms ± 0 ns per loop (mean ± std. dev. of 1 run, 1 loop each)


## `@njit` har mindre effekt med mer kompliserte datastrukturer

`@njit` fungerer best når funksjonen (og alle funksjoner som kalles inni) kun bruker arrayer og skalarer til å håndtere data, siden de har en fast lengde og kan representeres enkelt på maskinnivå. Lister, for eksempel, er mer kompliserte siden de ikke har en forhåndsdefinert lengde.

Følgende variant av `fibonacci` lagrer verdiene i en liste istendefor en array.

In [162]:
def fibonacci_list(N):
    """
    Computes the Fibonacci sequence with N elements.
    Grows a list instead of inserting into an array.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = [0.0, 1.0]
    for i in range(2, N):
        a.append(a[i-1] + a[i-2])
    return a

In [163]:
%timeit fibonacci_list(1000)

51.6 μs ± 525 ns per loop (mean ± std. dev. of 7 runs, 10,000 loops each)


In [164]:
@njit
def fibonacci_list_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    Grows a list instead of inserting into an array.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = [0.0, 1.0]
    for i in range(2, N):
        a.append(a[i-1] + a[i-2])
    return a

Den `@njit`ede versjonen går litt raskere, men ikke så veldig mye.

In [165]:
%timeit fibonacci_list_jit(1000) # ~7 times faster than fibonacci_list

16.3 μs ± 245 ns per loop (mean ± std. dev. of 7 runs, 100,000 loops each)


Du burde unngå kompliserte datastrukturer som dictionaries med `@njit`. Du kan ofte enten få en feilmelding, eller at koden bare ikke går raskere.

Her er en variant av `fibonacci` lagrer verdiene i en `dict` istedenfor en array.

In [166]:
def fibonacci_dict(N):
    """
    Computes the Fibonacci sequence with N elements.
    Builds a dictionary instead of inserting into an array.
    (This is a very stupid way of using a dictionary..)
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = {0: 0.0, 1: 1.0}
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

In [167]:
%timeit fibonacci_dict(1000)

58.5 μs ± 355 ns per loop (mean ± std. dev. of 7 runs, 10,000 loops each)


In [168]:
@njit
def fibonacci_dict_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    Builds a dictionary instead of inserting into an array.
    (This is a very stupid way of using a dictionary..)
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = {0: 0.0, 1: 1.0}
    for i in range(2, N):
        a[i] = a[i-1] + a[i-2]
    return a

Koden kjører ikke noe særlig raskere:

In [169]:
%timeit fibonacci_dict_jit(1000)

35.3 μs ± 218 ns per loop (mean ± std. dev. of 7 runs, 10,000 loops each)


## `@njit` på funksjoner med bugs kan ha katastrofale konsekvenser

Husk at du **alltid** må teste at funksjonen din fungerer som den skal **før** du bruker `@njit` på den. Dette gjelder også hver gang du endrer noe i funksjonen senere, **kommenter ut `@njit` hver gang du modifiserer funksjonen og ikke aktiver det igjen før du vet at ting fungerer!**

Det er i prinsippet ikke noe problem å endre ting mens funksjonen er `@njit`et, neste gang den kalles vil den oversettes på nytt og endringene vil tre i kraft. Problemet er at `@njit`et kode kan gi kryptiske feilmeldinger som følge av problemer som ikke egentlig har noe med `@njit` å gjøre i det hele tatt, eller enda verre, la være å gi feilmeldinger selv om ting går galt!

Et skrekkeksempel på dette kan du se her.

In [170]:
def fibonacci_buggy(N):
    """
    Computes the Fibonacci sequence with N elements.
    WARNING: THIS CODE HAS A MISTAKE!
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N+1): # Whoops, should be range(2, N)
        a[i] = a[i-1] + a[i-2]
    return a

I `fibonacci_buggy` har den øvre grensen i `for`-løkken ved en feiltagelse blitt satt til `N+1` istedenfor `N`. Dette medfører at koden vil prøve å skrive til `a[N]` i siste iterasjon, som er ugyldig siden siste element i arrayen er `a[N-1]`. Men dette sier heldigvis Python tydelig ifra om.

In [171]:
try:
    print(fibonacci_buggy(5)) # Saved by bounds check
except IndexError as e:
    print(e)

index 5 is out of bounds for axis 0 with size 5


Men hvordan går dette i den `@njit`ede versjonen?

In [172]:
@jit(nopython=True)
def fibonacci_buggy_jit(N):
    """
    Computes the Fibonacci sequence with N elements.
    WARNING: THIS CODE HAS A MISTAKE!
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N+1): # Whoops, should be range(2, N)
        a[i] = a[i-1] + a[i-2]
    return a

In [173]:
try:
    print(fibonacci_buggy_jit(5)) # Uh oh, anything can happen now
except IndexError as e:
    print(e)

[0. 1. 1. 2. 3.]


Ingen feilmelding.. Men det betyr at koden fikk lov å skrive utenfor arrayen. Dette virker kanskje uskyldig nok, men tenk på hva det innebærer. Hva som helst av informasjon som programmet benytter til å kjøre kan ha vært lagret på minneadressen som vi akkurat overskrev, det være seg kodeinstrukser eller variabler. Det betyr at det ikke er noen måte å forutse hva programmet vil finne på! Og utfallet vil variere med tiden, månefasen og hva du lytter til på Spotify. Vi har støtt på enhver feilsøkers verste mareritt: **udefinert oppførsel**!

Moralen er at `@njit` skal holdes langt unna kode som du ikke først har testet at fungerer. Og hvis du mistenker at noe er galt bør det første du gjør være å fjerne `@njit` før du feilsøker.

## Andre fallgruver

### Kalle funksjoner som er definert uten `@njit`

In [174]:
def fibonacci_nested(N):
    return fibonacci(N) # fibonacci is not @jit'ed

In [175]:
print(fibonacci_nested(5))

[0. 1. 1. 2. 3.]


In [176]:
@jit(nopython=True)
def fibonacci_nested_jit(N):
    return fibonacci(N) # fibonacci is not @jit'ed

In [177]:
try:
    print(fibonacci_nested_jit(5)) # TypingError: Failed in nopython mode pipeline
except nb.TypingError as e:
    print(e)

Failed in nopython mode pipeline (step: nopython frontend)
Untyped global name 'fibonacci': Cannot determine Numba type of <class 'function'>

File "../../../../../../tmp/ipykernel_13831/2692440307.py", line 3:
<source missing, REPL/exec in use?>



In [178]:
@njit
def fibonacci_nested_jit_working(N):
    return fibonacci_jit(N) # fibonacci_jit is @jit'ed

In [179]:
print(fibonacci_nested_jit_working(5))

[0. 1. 1. 2. 3.]


### Sende inn en funksjon som argument

In [111]:
def fibonacci_custom_operator(N, operation):
    """
    Computes the Fibonacci sequence with N elements.
    The argument `operation` is a function that combines two numbers into one.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = operation(a[i-1], a[i-2]) # Uses inputted function to combine elements
    return a

In [112]:
print(fibonacci_custom_operator(5, lambda a, b: a + b))

[0. 1. 1. 2. 3.]


In [113]:
@njit
def fibonacci_custom_operator_jit(N, operation):
    """
    Computes the Fibonacci sequence with N elements.
    The argument `operation` is a function that combines two numbers into one.
    """
    assert N >= 2, 'N cannot be smaller than 2'
    a = np.zeros(N)
    a[1] = 1.0
    for i in range(2, N):
        a[i] = operation(a[i-1], a[i-2]) # Uses inputted function to combine elements
    return a

In [114]:
try:
    print(fibonacci_custom_operator_jit(5, lambda a, b: a + b)) # TypingError: Failed in nopython mode pipeline
except nb.TypingError as e:
    print(e)

Failed in nopython mode pipeline (step: nopython frontend)
non-precise type pyobject
During: typing of argument at /tmp/ipykernel_13831/784381445.py (1)

File "../../../../../../tmp/ipykernel_13831/784381445.py", line 1:
<source missing, REPL/exec in use?> 

This error may have been caused by the following argument(s):
- argument 1: Cannot determine Numba type of <class 'function'>



# Parallelisering med Numba
Noen ganger kan vi gjøre koden enda raskere ved å "parallelisere" den. Hvis vi har en vanlig loop med "range", kan vi bytte ut dette med Numba sin "prange", og bruke @njit(parallelize=True). CPUen din vil da kjøre noen av loop-iterasjonene *samtidig*, (f.eks. 1-8 på en gang, så 9-16 på en gang...). Vi må da være veldig forsiktige med at loop-interasjonene *kan* kjøre samtidig uten at det gir feil svar!

Her er et eksempel på en enkel kode som summer sammen to arrays (med noe sinuer og log-er), og returnerer den summede arrayen:

In [221]:
@njit
def sum_loop(array1, array2):
    array_out = np.zeros_like(array1)
    for i in range(array1.shape[0]):
        array_out[i] = 0.5*np.sin(array1[i]) + np.log(array2[i]) - 1.0
    return array_out

In [222]:
array1 = np.random.normal(0, 1, int(1e6))
array2 = np.random.normal(0, 1, int(1e6))

In [223]:
%timeit sum_loop(array1, array2)

17.2 ms ± 62.2 μs per loop (mean ± std. dev. of 7 runs, 100 loops each)


Fordi hver loop-iterasjon skriver til forskjellige indekser i arrayen, og de er helt uavhengige, kan vi lage en parallelisert versjon av denne koden: 

In [224]:
@njit(parallel=True)
def sum_loop_parallel(array1, array2):
    array_out = np.zeros_like(array1)
    for i in prange(array1.shape[0]):
        array_out[i] = 0.5*np.sin(array1[i]) + np.log(array2[i]) - 1.0
    return array_out 

Den kjører enda raskere!

In [225]:
%timeit sum_loop_parallel(array1, array2)

2.63 ms ± 28.1 μs per loop (mean ± std. dev. of 7 runs, 100 loops each)


# Når kan vi IKKE parallelisere med Numba

La oss endre litt på funksjonen, så element nummer i avhenger av element i-1:

In [194]:
@njit
def sum_new(array):
    # A Numba loop, where the results of array_out[i] depends on array_out[i-1]
    array_out = np.zeros_like(array)
    for i in range(array.shape[0]):
        array_out[i] = array[i] + array_out[i-1]
    return array_out

Da kan vi IKKE parallelisere med Numba, fordi loop-iterasjonene ikke kan utføres samtidig!

In [195]:
@njit(parallel=True)
def sum_new_parallel(array):
    # A Numba loop, where the results of array_out[i] depends on array_out[i-1]
    array_out = np.zeros_like(array)
    for i in prange(array.shape[0]):
        array_out[i] = array[i] + array_out[i-1]
    return array_out

De to arraysene blir forskjellige:

In [196]:
print(sum_new(array1))
print(sum_new_parallel(array1))

[-7.87331452e-01 -7.62527073e-01 -1.85739584e+00 ...  1.05895945e+03
  1.05941475e+03  1.06023235e+03]
[ -0.78733145  -0.76252707  -1.85739584 ... 336.86113906 337.31643762
 338.13403105]
